# Salary estimator from listings

## Setup

To begin we will install all the necessary packages for the application to run. We can do that by running the block of code below that uses IPython commands to install the packages. Press the play button to the left of the code block.

In [1]:
%%capture
%pip install "scipy==1.12" pandas xgboost scikit-learn gensim pyarrow plotly Jinja2 nbformat ipywidgets

Next we will download and extract the data.

Download the data from kaggle. https://www.kaggle.com/datasets/arshkon/linkedin-job-postings

Then run the code below to determine where to extract the zip file.

In [2]:
import settings
print('Extract the archive data to this path:', settings.ARCHIVE_PATH)

Extract the archive data to this path: c:\dev\job-estimator/archive


Next extract the zip folder to the path above. You may need to close the IDE you are using before you can extract to that location.

After it is extracted to the correct directory, we will create a directory in our archive that will store changes to our dataset. It can be time consuming to reload all our data every time we need to restart the app. After the first run, the directory will help reduce the time it takes for the entire app to run.

In [3]:
import os, settings
if not os.path.exists(settings.APP_ARCHIVE_PATH):
    os.makedirs(settings.APP_ARCHIVE_PATH)

## Parsing and cleaning the data
After our folders and data are set up, we can start parsing the data! First we will instantiate the DataManager class. It will handle reading the csv files, joining the data, dropping unnecessary columns, renaming confusing columns, parsing which state the jobs are in, getting the average pay for each job, transforming different pay periods to yearly salary for consistency, dropping duplicates, and saving the cleaned, transformed job postings.

In [4]:
from data import DataManager

dm = DataManager()
df = dm.get_postings()

Importing libraries for the DataManager class.
Reading tables
Joining tables
Dropping unhelpful columns.
Renaming confusing columns.
Creating a state abbreviation column from the location column and normalizing the pay columns.
Setting outlier pay column values to NaN.
Creating an average salary column that is is the average of the salary pay columns. ['max_salary', 'med_salary', 'min_salary']
Dropping duplicate jobs based on these colums: job_title, company_name, job_desc, state, pay, listed_time.
Saving cleaned the posting table so we do not need to process it each time.


Now that the data is cleaned let's look at a random posting. We will shorten some of the text columns so we can fit most of it on the screen. You can use the horizontal scroll bar to see more columns.

In [5]:
from IPython.display import HTML, display

df = dm.get_postings()
def shorten_long_cols(row):
    for name in ['job_desc','company_desc','skills_desc']:
        if isinstance(row[name], str):
            row[name] = row[name][:150] + '...' 
    return row

display(HTML(df.sample(3).apply(shorten_long_cols, axis=1).to_html()))

There are a few important items we should pay attention to. 

1. The location column which is the location of the job is not normalized to a state abbreviation. Usually it's in the format "City, State" but that is not always the case. The state column was originally the location of the company. Jobs may be located in states other than where the company HQ resides. So we use some regex and code in the DataManager to extract the state and translate it to a state abbreviation, then save it to the state column. If we can't extract a state from the location column, we fall back to using the company state column. 

2. Job titles are generaly unique. This could cause some issues for us when we try to use regression to estimate salaries for job titles. If the XGBoost model receives data with high cardinality, it will be much less accurate. So we need to create word embeddings to represent the job titles and reduce the complexity of the job titles. We will use the Word2Vec model to generate vectors from words and use the vectors to represent the job titles with XGBoost.

3. We can use the job_title, job_desc, job_skills, skills_desc, and company_desc to train the word2vec model. We need a lot of data to make the vectors, so we can use the plethora of text from these columns to train it.

4. The pay_period and salary columns include data for different pay periods. If we train the model with inconsistent pay information, it will not be able to accurately estimate pay. We needed to normalize those columns. So the DataManager class converts all pay periods to yearly pay. For most pay periods it multiplies the pay to make it represent a year's worth of pay. e.g., monthly pay times twelve equals yearly pay. For hourly pay, we must account for time off, full-time/part-time hours, and holidays. The DataManager uses statistics from the Bureau of Labor Statistics to calculate the average full-time and part-time working hours per week and working weeks per year. Then it multiplies those with the pay to create the job yearly pay.

5. It also takes the average between the max, med, and min salary columns if they exist. Additionally the salary columns with 0 at the end of their names come from the salaries csv file. So if the main salary columns are empty, the DataManager uses the back up columns to calculate the pay. After it finishes normalizing the pay columns, it saves the results to the "pay" column.

### Descriptive statistics of the pay data.

In [6]:
pay_cols = ['max_salary','med_salary','min_salary','pay']
pay_period_df = dm.get_postings()[pay_cols]
desc = pay_period_df.describe()

message = '<div style="font-size:18px"><p>There are a few interesting feature in the pay statistics. First, the "pay" column is a calculated column the DataManager created earlier.</p>'
for col in pay_cols:
    message += '''<p>
    There are {count:,.0f} {col} values. The average {col} is ${mean:,.0f} and the standard deviation is {std:,.0f}. The {col} column has a minimum of ${min:,.0f}, median of ${50%:,.0f} and a maximum of ${max:,.0f}. 
    25% of the {col} values are less than ${25%:,.0f} and 25% are greater than ${75%:,.0f}. 
    So 50% of the values are between ${25%:,.0f} and ${75%:,.0f}.
    </p>'''.format(col=col, **desc[col])

message += '''<p>
The columns values are not completely filled out because there are more max and min salary values than med_salary values.
Additionally, many jobs do not have an pay information because the number of pay values is much less than the total number of jobs.
</p></div>'''
display(HTML(desc.style.format(precision=0,thousands=",").to_html()))
display(HTML(message))

In [20]:
import plotly.graph_objects as go
fig = go.Figure(layout=dict(height=800, title='Job Posting Pay Column Box Plots'))
fig.add_traces([go.Box(y=pay_period_df[col], boxpoints=False, jitter=.3, name=col) for col in pay_cols])
fig.update_yaxes(tickprefix = '$', tickformat = ',.0f', type="log",automargin=True)
fig.show()

The box plots above represent the descriptive statistics we generated earlier.

Next we will create a bar graph of average salaries by state.

In [8]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

df = dm.get_postings()[['state','pay']].copy().dropna(how='any')

groups = df.groupby('state')
group_count = groups.count()
df = groups.mean()
df['count'] = group_count
df = df.dropna(axis=1).sort_values(by='pay')

fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Bar(
        x = df.index.values, 
        y=df['pay'],
        name="Average Yearly Pay",
    ), 
    secondary_y=False)

fig.add_trace(
    go.Scatter(
        x = df.index.values,
        y = df['count'],
        name="Sample Size"
    ),
    secondary_y=True
)

fig.update_layout(
    title=dict(text="Average Job Posting Pay By State"),
    xaxis=dict(title_text="State",tickangle=90),
    yaxis=dict(title_text="Average Yearly Pay")
)

fig.update_yaxes(title_text="Job Listings (log)", secondary_y=True, type="log")

fig.show()

The bars represent the average yearly pay in each state. The red line represents the number of job listings for that state. Some states have a very low amount of job listings. Our pay estimates in those states will be less accurate. Specifically Wyoming has the least job listings at 26. Additionally the states with the most listings will skew the overall dataset statistics the most. California has the most listings at 6615. The state with the minimum average pay is Mississippi with an average pay of $66,143.50. Washington DC has the highest average pay at $110,660.20.

Now we should see what the average pay is for different jobs. Since the job titles have a high cardinality, we can not reasonably display them on an axis in a chart. So before we try to get the averages, we need to sort the job postings into categories.

### Create a dataset
Instatiate the Job2Vec class. It is a wrapper to preprocess data and train the Word2Vec word embedding model.

In [9]:
from wordmod import Job2Vec

job2vec = Job2Vec()

Get or train the word embedding model.

If there is not already tokenized strings, make a list of the strings we will use to train Word2Vec. Then tokenize the list of strings because Word2Vec takes a list of list of strings. list[list[str]]

In [10]:
import numpy as np

print('Loading j2v word vectors.')
j2v = job2vec.try_get_model()

if j2v is None:
    dataset = job2vec.try_load_dataset()

    if dataset is None:
        df = dm.get_postings().copy()

        print("Combining the the bls.gov job list, LinkedIn job title, description and skills, columns, and other tables to create a single array. Word2Vec does not need them separated.")
        bls = dm.get_bls_jobs().to_numpy()
        others = np.concatenate(dm.load_additional_tables())
        data = [bls, others, df['job_title'].unique(), df['job_desc'].unique(), df['skills_desc'].unique(), df['company_desc'].unique()]
        ser = np.concatenate(data)

        dataset = job2vec.preprocess_data(ser)
    
    j2v = job2vec.try_get_model(dataset)


Loading j2v word vectors.
Retrieving an existing model from c:\dev\job-estimator/assets/models/w2v.model


Use the word embedding model to compare word vectors and categorize jobs.

In [11]:
from catword import Categorizer
import pandas as pd

categorizer = Categorizer(j2v.wv, job2vec.tokenize)

In [12]:
df = dm.get_or_create_categorized_postings(categorizer.categorize)

groups = df[['pay', 'category']].dropna(how='all').groupby('category')
fig_df = groups.mean(numeric_only=True).sort_values(by='pay')
fig_df['count'] = groups.count()

fig = make_subplots(specs=[[{"secondary_y": True}]])

fig = fig.add_trace(go.Bar(x=fig_df.index.values, y=fig_df['pay'], name='Average Pay'))

fig.update_layout(
    title=dict(text="Average Job Posting Pay By Category"),
    yaxis=dict(title_text="Average Yearly Pay")
)

fig.add_trace(
    go.Scatter(
        x = fig_df.index.values,
        y = fig_df['count'],
        name="Sample Size"
    ),
    secondary_y=True
)

fig.update_yaxes(title_text="Job Listings (log)", secondary_y=True, type="log")

fig.show()

Retrieving categorized jobs from file c:\dev\job-estimator/archive/app/categorized_postings.pqt


In [13]:
import plotly.express as px

df = dm.get_or_create_categorized_postings(categorizer.categorize).copy()
df['id'] = df.index.values
g = df[['category','state','id']]
fig_df = g.groupby(by=['state','category'], group_keys=False).size().reset_index()

fig = px.scatter_3d(fig_df, x='state', y='category', z=0, color=0)
fig.update_layout(
    height=800,
    xaxis=dict(nticks=51),
    yaxis=dict(nticks=51),
    margin={"t":0,"b":0}
)
fig.update_scenes(aspectmode='cube')
fig.show()

Retrieving categorized jobs from file c:\dev\job-estimator/archive/app/categorized_postings.pqt


### XGBoost training pipeline

In [14]:
    
from sklearn.model_selection import train_test_split
df = dm.get_postings().copy()
x_cols=['state',
        'job_title']
y_col = 'pay'

mask = df[['job_title', 'state', y_col]].notna().all(axis=1) & df[y_col].gt(0)
df = df[x_cols+[y_col]].loc[mask].copy().reset_index()

x, y = df[x_cols], df[y_col]
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=.1)

In [15]:
import pandas as pd
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder, FunctionTransformer


vector_length = j2v.wv.vector_size

def title_to_vec(titles: pd.DataFrame):
    vector_cols = [f'title{n}' for n in range(vector_length)]
    rows = [job2vec.vectorize(x) for x in titles['job_title'].values]
    return pd.DataFrame(rows, columns=vector_cols)

non_title_cols = ['state']

preprocessor = ColumnTransformer(transformers=[
    ("cat", OneHotEncoder(handle_unknown="ignore"), non_title_cols),
    ("title", FunctionTransformer(title_to_vec), ['job_title'])
])

preprocessor = preprocessor.fit(x,y)

In [16]:
import xgboost as xgb
import os, settings

xgb_reg: xgb.XGBRegressor = xgb.XGBRegressor(
    device='cuda:2',
    booster='gbtree',
    tree_method= 'hist',
    objective='reg:squarederror',
    eval_metric='mae',
    eta=0.1, 
    max_depth=20,
    early_stopping_rounds=15,
    verbosity=0,
    n_estimators=500
)

xgb_pipe = Pipeline(steps=[
    ("preprocess", preprocessor),
    ('reg', xgb_reg)
])

if os.path.isfile(settings.XGB_MODEL):
    xgb_reg.load_model(settings.XGB_MODEL)
    
else:
    x_test_preprocessed = preprocessor.transform(x_test)
    
    xgb_pipe = xgb_pipe.fit(
        x_train, 
        y_train, 
        reg__eval_set=[(x_test_preprocessed, y_test)])
    
    xgb_reg.save_model(settings.XGB_MODEL)

In [17]:
test = pd.DataFrame(x_test, columns=['state','job_title'])
test['pay'] = y_test
test = test.sample(10)
res = xgb_pipe.predict(test[x_cols])
test['predicted']=res
display(HTML(test.style.format(precision=2,thousands=",").to_html())) 

In [18]:
import ipywidgets as widgets
import json, locale
locale.setlocale(locale.LC_ALL, '')

title = None

states = dict(json.load(open(settings.STATE_ABBR)))
state_options = dict([(name, states[name]) for name in states])
state = state_options['CALIFORNIA']

def estimate_job_salary(title, state):
    similar = ', '.join(w[0] for w in j2v.wv.similar_by_vector(job2vec.vectorize(title)) if w[0] not in title and w[1] > .6) or 'No close similarities, results will likely be inaccurate.'

    result = xgb_pipe.predict(pd.DataFrame({'state':[state], 'job_title':[title]}))
    hourly_pay = locale.currency(dm.salary_to_hourly(result[0], 'HOURLY'), grouping=True)
    salary_pay = locale.currency(result[0], grouping=True)
    
    
    return display(HTML(fr'''
                        <table>
                            <tr>
                                <td>Salary pay:</td> 
                                <td>{salary_pay}</td>
                            </tr>
                            <tr>
                                <td>Hourly pay:</td> 
                                <td>{hourly_pay}</td>
                            </tr>
                            <tr>
                                <td>Similar words:</td>
                                <td>{similar}</td>
                            </tr>
                        </table>
                        '''))

w = widgets.interactive(estimate_job_salary, title='', state=state_options)
w

interactive(children=(Text(value='', description='title'), Dropdown(description='state', options={'ALASKA': 'A…